# Games Release data set (with PyQrack quantum associative memory)

"PyQrack" is a pure Python language standard wrapper for the (C++11) Qrack quantum computer simulator library. PyQrack exposes a "quantum neuron" called "`QrackNeuron`." (Its API reference is [here](https://pyqrack.readthedocs.io/en/latest/autoapi/pyqrack/qrack_neuron/index.html).) We'd like to model a simple data set to achieve a proof-of-concept of using `QrackNeuron`.

First, load the data set into a `pandas` dataframe.

In [1]:
import pandas as pd

df = pd.read_csv('games-release/games-release-ALL.csv')
df = df.loc[:, ~df.columns.str.contains('^Unnamed')]

df = df.drop(['game', 'link', 'release', 'total_reviews'], axis=1)

df['peak_players'] = df['peak_players'].str.replace(',', '').astype(int)
df['positive_reviews'] = df['positive_reviews'].str.replace(',', '').astype(int)
df['negative_reviews'] = df['negative_reviews'].str.replace(',', '').astype(int)
df['rating'] = df['rating'].str.replace('%', '').astype(float)

print(df.head())
print("Number of observations: ", df.shape[0])

   peak_players  positive_reviews  negative_reviews  rating
0          4529             19807               227   96.39
1        168191             61752              1616   95.75
2         15543             12643               213   95.54
3          1415             11717               209   95.39
4          6132             14152               324   95.09
Number of observations:  66427


Separate the dependent and independent variables.

In [2]:
keys = ['peak_players', 'positive_reviews', 'negative_reviews']
dep_key = 'rating'

X = df[keys]
y = df[dep_key] 

Ideally, we'd like to make an improvement on the goodness-of-fit of multiple linear regression, with PyQrack's `QrackNeuron`. At the very least, to show that `QrackNeuron` can be viable for modeling a data set, we'd like to show somehwat comparable performance to multiple linear regression.

PyQrack's `QrackNeuron` can only work with discrete, binary data. To model this or any data set, we have to reduce it to a simple, discrete, binary form.

We'll try to model the data set via "(quantum) associative memory." There are several statistical considerations, to avoid overfit.

Firstly, each possible discretized independent variable permutation input trains an independent parameter of a `QrackNeuron`. If a `QrackNeuron` has never seen a specific, exact permutation of input bits, it has no information about them at all, so its prediction defaults to "maximal superposition," (i.e. a totally random guess). Therefore, we'd like to keep our number of possible distinct inputs significantly fewer in number than our observation rows, when we discretize our indepedent variables.

Satisfying the first consideration, we secondly discretize our dependent variable to have exactly as many possible discrete values as possible distinct inputs. (We guess that this loses the least information about the dependent variable, while we still have enough observations to fully train our network.)

Thirdly, our learning rate should should just barely "saturate" the learned parameters of our (quantum) associative memory. As a learning volatility parameter ("`eta`") of `1/2` "fully trains" one parameter of a `QrackNeuron` between input qubits and output qubit, on average, this implies that we might set `eta` to `1/2` times `2` to the power of input qubits (summed across all predictors) divided by the number of observations. 

Start by splitting the data set into equal halves for training and validation.

In [3]:
train=df.sample(frac = 1/2)
test=df.drop(train.index)
train = train.reset_index(drop=True)
test = test.reset_index(drop=True)

X = train[keys]
y = train[dep_key]

X_test = test[keys]
y_test = test[dep_key]

At a baseline, our first choice to model this data set might be multiple linear regression.

In [4]:
from sklearn import linear_model

regr = linear_model.LinearRegression()
regr.fit(X, y)
pd.DataFrame(zip(X.columns, regr.coef_))

0         1
0      peak_players  0.000020
1  positive_reviews  0.000126
2  negative_reviews -0.000403

In [5]:
y_pred = regr.predict(X)
sst = 0
ssr = 0
for i in range(len(y_pred)):
    sst += y[i] * y[i]
    ssr += (y[i] - y_pred[i]) * (y[i] - y_pred[i])

print("Multiple linear regression training R^2: ", 1 - ssr / sst)

Multiple linear regression training R^2:  0.9564859432594576


In [6]:
y_pred = regr.predict(X_test)
sst = 0
ssr = 0
for i in range(len(y_pred)):
    sst += y_test[i] * y_test[i]
    ssr += (y_test[i] - y_pred[i]) * (y_test[i] - y_pred[i])

print("Multiple linear regression validation R^2: ", 1 - ssr / sst)

Multiple linear regression validation R^2:  0.9547922367566187


To discretize the data, we split it into as many quantiles as `2` to the power of our number of input qubits.

In [7]:
import numpy as np

in_qubit_count = 4

in_key_count = len(keys)
in_bin_count = 1 << in_qubit_count
in_tot_count = in_key_count * in_qubit_count
out_qubit_count = in_key_count * in_qubit_count
out_bin_count = 1 << out_qubit_count

x_bins = []
for key in keys:
    x_bins.append(np.percentile(X[key], np.arange(0, 100, 100 / in_bin_count)))
y_bins = np.percentile(y, np.arange(0, 100, 100 / out_bin_count))

In [8]:
print(x_bins)

[array([0.0000000e+00, 1.0000000e+00, 2.0000000e+00, 2.0000000e+00,
       3.0000000e+00, 3.0000000e+00, 4.0000000e+00, 5.0000000e+00,
       6.0000000e+00, 9.0000000e+00, 1.3000000e+01, 2.3000000e+01,
       4.5000000e+01, 1.0500000e+02, 2.7200000e+02, 1.0975625e+03]), array([0.0000000e+00, 1.0000000e+00, 2.0000000e+00, 3.0000000e+00,
       5.0000000e+00, 7.0000000e+00, 1.0000000e+01, 1.4000000e+01,
       1.9000000e+01, 2.6000000e+01, 3.8000000e+01, 5.8000000e+01,
       9.7000000e+01, 1.8200000e+02, 4.0700000e+02, 1.3711875e+03]), array([  0.,   0.,   0.,   1.,   1.,   2.,   3.,   4.,   6.,   8.,  12.,
        18.,  28.,  49., 101., 285.])]


In [9]:
print(y_bins)

[15.09       20.46       21.2843457  ... 95.70674072 95.8856543
 96.42348145]


Once we have our quantiles, we bin our indepedent training and validation data.

In [10]:
def discretize_x(X):
    xd = []
    for i in X.index:
        xd_row = []
        for ki in range(len(keys)):
            key = keys[ki]
            bn = in_bin_count
            offset = 0
            while bn > 1:
                bn =  bn // 2
                b = bn + offset
                if X[key][i] < x_bins[ki][b - 1]:
                    xd_row.append(False)
                else:
                    xd_row.append(True)
                    offset += bn
        xd.append(xd_row)
    return xd

xd = discretize_x(X)
xd_test = discretize_x(X_test)

We do the same for our dependent data.

In [11]:
def discretize_y(y):
    yd = []
    for i in y.index:
        yd_row = []
        bn = out_bin_count
        offset = 0
        while bn > 0:
            bn =  bn // 2
            b = bn + offset
            if y[i] < y_bins[b - 1]:
                yd_row.append(False)
            else:
                yd_row.append(True)
                offset += bn
        yd.append(yd_row)
    return yd

yd = discretize_y(y)
yd_test = discretize_y(y_test)

We're ready to train our associative memory! (Note that it offers us no particular advantage, in this case, that our "neurons" are based on simulated quantum computational gates, though it is possible to predict in "superposition" of many rows at once.)

In [12]:
from pyqrack import QrackSimulator, QrackNeuron

eta = (1 / 2) * (out_bin_count / y.shape[0])

input_power = 1 << in_tot_count
input_indices = list(range(in_tot_count))
qsim = QrackSimulator(in_tot_count + out_qubit_count)

output_layer = []
for i in range(out_qubit_count):
    output_layer.append(QrackNeuron(qsim, input_indices, in_tot_count + i))

# Train the network to associate powers of 2 with their log2()
print("Learning...")
for i in range(len(xd)):
    perm = xd[i]
    res = yd[i]

    print("Epoch ", (i + 1), " out of ", len(xd))
    for j in range(out_qubit_count):
        qsim.reset_all()
        for k in range(in_tot_count):
            if perm[k]:
                qsim.x(k)
        for k in range(out_qubit_count):
            if res[k]:
                qsim.x(in_tot_count + k)
        output_layer[j].learn_permutation(eta, res[j] == 1)

Device #0, Loaded binary from: /home/iamu/.qrack/qrack_ocl_dev_Intel(R)_UHD_Graphics_[0x9bc4].ir
Device #1, Loaded binary from: /home/iamu/.qrack/qrack_ocl_dev_NVIDIA_GeForce_RTX_3080_Laptop_GPU.ir
Learning...
Epoch  1  out of  33214
Epoch  2  out of  33214
Epoch  3  out of  33214
Epoch  4  out of  33214
Epoch  5  out of  33214
Epoch  6  out of  33214
Epoch  7  out of  33214
Epoch  8  out of  33214
Epoch  9  out of  33214
Epoch  10  out of  33214
Epoch  11  out of  33214
Epoch  12  out of  33214
Epoch  13  out of  33214
Epoch  14  out of  33214
Epoch  15  out of  33214
Epoch  16  out of  33214
Epoch  17  out of  33214
Epoch  18  out of  33214
Epoch  19  out of  33214
Epoch  20  out of  33214
Epoch  21  out of  33214
Epoch  22  out of  33214
Epoch  23  out of  33214
Epoch  24  out of  33214
Epoch  25  out of  33214
Epoch  26  out of  33214
Epoch  27  out of  33214
Epoch  28  out of  33214
Epoch  29  out of  33214
Epoch  30  out of  33214
Epoch  31  out of  33214
Epoch  32  out of  33214

Epoch  410  out of  33214
Epoch  411  out of  33214
Epoch  412  out of  33214
Epoch  413  out of  33214
Epoch  414  out of  33214
Epoch  415  out of  33214
Epoch  416  out of  33214
Epoch  417  out of  33214
Epoch  418  out of  33214
Epoch  419  out of  33214
Epoch  420  out of  33214
Epoch  421  out of  33214
Epoch  422  out of  33214
Epoch  423  out of  33214
Epoch  424  out of  33214
Epoch  425  out of  33214
Epoch  426  out of  33214
Epoch  427  out of  33214
Epoch  428  out of  33214
Epoch  429  out of  33214
Epoch  430  out of  33214
Epoch  431  out of  33214
Epoch  432  out of  33214
Epoch  433  out of  33214
Epoch  434  out of  33214
Epoch  435  out of  33214
Epoch  436  out of  33214
Epoch  437  out of  33214
Epoch  438  out of  33214
Epoch  439  out of  33214
Epoch  440  out of  33214
Epoch  441  out of  33214
Epoch  442  out of  33214
Epoch  443  out of  33214
Epoch  444  out of  33214
Epoch  445  out of  33214
Epoch  446  out of  33214
Epoch  447  out of  33214
Epoch  448  

Epoch  747  out of  33214
Epoch  748  out of  33214
Epoch  749  out of  33214
Epoch  750  out of  33214
Epoch  751  out of  33214
Epoch  752  out of  33214
Epoch  753  out of  33214
Epoch  754  out of  33214
Epoch  755  out of  33214
Epoch  756  out of  33214
Epoch  757  out of  33214
Epoch  758  out of  33214
Epoch  759  out of  33214
Epoch  760  out of  33214
Epoch  761  out of  33214
Epoch  762  out of  33214
Epoch  763  out of  33214
Epoch  764  out of  33214
Epoch  765  out of  33214
Epoch  766  out of  33214
Epoch  767  out of  33214
Epoch  768  out of  33214
Epoch  769  out of  33214
Epoch  770  out of  33214
Epoch  771  out of  33214
Epoch  772  out of  33214
Epoch  773  out of  33214
Epoch  774  out of  33214
Epoch  775  out of  33214
Epoch  776  out of  33214
Epoch  777  out of  33214
Epoch  778  out of  33214
Epoch  779  out of  33214
Epoch  780  out of  33214
Epoch  781  out of  33214
Epoch  782  out of  33214
Epoch  783  out of  33214
Epoch  784  out of  33214
Epoch  785  

Epoch  1076  out of  33214
Epoch  1077  out of  33214
Epoch  1078  out of  33214
Epoch  1079  out of  33214
Epoch  1080  out of  33214
Epoch  1081  out of  33214
Epoch  1082  out of  33214
Epoch  1083  out of  33214
Epoch  1084  out of  33214
Epoch  1085  out of  33214
Epoch  1086  out of  33214
Epoch  1087  out of  33214
Epoch  1088  out of  33214
Epoch  1089  out of  33214
Epoch  1090  out of  33214
Epoch  1091  out of  33214
Epoch  1092  out of  33214
Epoch  1093  out of  33214
Epoch  1094  out of  33214
Epoch  1095  out of  33214
Epoch  1096  out of  33214
Epoch  1097  out of  33214
Epoch  1098  out of  33214
Epoch  1099  out of  33214
Epoch  1100  out of  33214
Epoch  1101  out of  33214
Epoch  1102  out of  33214
Epoch  1103  out of  33214
Epoch  1104  out of  33214
Epoch  1105  out of  33214
Epoch  1106  out of  33214
Epoch  1107  out of  33214
Epoch  1108  out of  33214
Epoch  1109  out of  33214
Epoch  1110  out of  33214
Epoch  1111  out of  33214
Epoch  1112  out of  33214
E

Epoch  1407  out of  33214
Epoch  1408  out of  33214
Epoch  1409  out of  33214
Epoch  1410  out of  33214
Epoch  1411  out of  33214
Epoch  1412  out of  33214
Epoch  1413  out of  33214
Epoch  1414  out of  33214
Epoch  1415  out of  33214
Epoch  1416  out of  33214
Epoch  1417  out of  33214
Epoch  1418  out of  33214
Epoch  1419  out of  33214
Epoch  1420  out of  33214
Epoch  1421  out of  33214
Epoch  1422  out of  33214
Epoch  1423  out of  33214
Epoch  1424  out of  33214
Epoch  1425  out of  33214
Epoch  1426  out of  33214
Epoch  1427  out of  33214
Epoch  1428  out of  33214
Epoch  1429  out of  33214
Epoch  1430  out of  33214
Epoch  1431  out of  33214
Epoch  1432  out of  33214
Epoch  1433  out of  33214
Epoch  1434  out of  33214
Epoch  1435  out of  33214
Epoch  1436  out of  33214
Epoch  1437  out of  33214
Epoch  1438  out of  33214
Epoch  1439  out of  33214
Epoch  1440  out of  33214
Epoch  1441  out of  33214
Epoch  1442  out of  33214
Epoch  1443  out of  33214
E

...

Epoch  31936  out of  33214
Epoch  31937  out of  33214
Epoch  31938  out of  33214
Epoch  31939  out of  33214
Epoch  31940  out of  33214
Epoch  31941  out of  33214
Epoch  31942  out of  33214
Epoch  31943  out of  33214
Epoch  31944  out of  33214
Epoch  31945  out of  33214
Epoch  31946  out of  33214
Epoch  31947  out of  33214
Epoch  31948  out of  33214
Epoch  31949  out of  33214
Epoch  31950  out of  33214
Epoch  31951  out of  33214
Epoch  31952  out of  33214
Epoch  31953  out of  33214
Epoch  31954  out of  33214
Epoch  31955  out of  33214
Epoch  31956  out of  33214
Epoch  31957  out of  33214
Epoch  31958  out of  33214
Epoch  31959  out of  33214
Epoch  31960  out of  33214
Epoch  31961  out of  33214
Epoch  31962  out of  33214
Epoch  31963  out of  33214
Epoch  31964  out of  33214
Epoch  31965  out of  33214
Epoch  31966  out of  33214
Epoch  31967  out of  33214
Epoch  31968  out of  33214
Epoch  31969  out of  33214
Epoch  31970  out of  33214
Epoch  31971  out of

Epoch  32245  out of  33214
Epoch  32246  out of  33214
Epoch  32247  out of  33214
Epoch  32248  out of  33214
Epoch  32249  out of  33214
Epoch  32250  out of  33214
Epoch  32251  out of  33214
Epoch  32252  out of  33214
Epoch  32253  out of  33214
Epoch  32254  out of  33214
Epoch  32255  out of  33214
Epoch  32256  out of  33214
Epoch  32257  out of  33214
Epoch  32258  out of  33214
Epoch  32259  out of  33214
Epoch  32260  out of  33214
Epoch  32261  out of  33214
Epoch  32262  out of  33214
Epoch  32263  out of  33214
Epoch  32264  out of  33214
Epoch  32265  out of  33214
Epoch  32266  out of  33214
Epoch  32267  out of  33214
Epoch  32268  out of  33214
Epoch  32269  out of  33214
Epoch  32270  out of  33214
Epoch  32271  out of  33214
Epoch  32272  out of  33214
Epoch  32273  out of  33214
Epoch  32274  out of  33214
Epoch  32275  out of  33214
Epoch  32276  out of  33214
Epoch  32277  out of  33214
Epoch  32278  out of  33214
Epoch  32279  out of  33214
Epoch  32280  out of

Epoch  32553  out of  33214
Epoch  32554  out of  33214
Epoch  32555  out of  33214
Epoch  32556  out of  33214
Epoch  32557  out of  33214
Epoch  32558  out of  33214
Epoch  32559  out of  33214
Epoch  32560  out of  33214
Epoch  32561  out of  33214
Epoch  32562  out of  33214
Epoch  32563  out of  33214
Epoch  32564  out of  33214
Epoch  32565  out of  33214
Epoch  32566  out of  33214
Epoch  32567  out of  33214
Epoch  32568  out of  33214
Epoch  32569  out of  33214
Epoch  32570  out of  33214
Epoch  32571  out of  33214
Epoch  32572  out of  33214
Epoch  32573  out of  33214
Epoch  32574  out of  33214
Epoch  32575  out of  33214
Epoch  32576  out of  33214
Epoch  32577  out of  33214
Epoch  32578  out of  33214
Epoch  32579  out of  33214
Epoch  32580  out of  33214
Epoch  32581  out of  33214
Epoch  32582  out of  33214
Epoch  32583  out of  33214
Epoch  32584  out of  33214
Epoch  32585  out of  33214
Epoch  32586  out of  33214
Epoch  32587  out of  33214
Epoch  32588  out of

Epoch  32862  out of  33214
Epoch  32863  out of  33214
Epoch  32864  out of  33214
Epoch  32865  out of  33214
Epoch  32866  out of  33214
Epoch  32867  out of  33214
Epoch  32868  out of  33214
Epoch  32869  out of  33214
Epoch  32870  out of  33214
Epoch  32871  out of  33214
Epoch  32872  out of  33214
Epoch  32873  out of  33214
Epoch  32874  out of  33214
Epoch  32875  out of  33214
Epoch  32876  out of  33214
Epoch  32877  out of  33214
Epoch  32878  out of  33214
Epoch  32879  out of  33214
Epoch  32880  out of  33214
Epoch  32881  out of  33214
Epoch  32882  out of  33214
Epoch  32883  out of  33214
Epoch  32884  out of  33214
Epoch  32885  out of  33214
Epoch  32886  out of  33214
Epoch  32887  out of  33214
Epoch  32888  out of  33214
Epoch  32889  out of  33214
Epoch  32890  out of  33214
Epoch  32891  out of  33214
Epoch  32892  out of  33214
Epoch  32893  out of  33214
Epoch  32894  out of  33214
Epoch  32895  out of  33214
Epoch  32896  out of  33214
Epoch  32897  out of

Epoch  33171  out of  33214
Epoch  33172  out of  33214
Epoch  33173  out of  33214
Epoch  33174  out of  33214
Epoch  33175  out of  33214
Epoch  33176  out of  33214
Epoch  33177  out of  33214
Epoch  33178  out of  33214
Epoch  33179  out of  33214
Epoch  33180  out of  33214
Epoch  33181  out of  33214
Epoch  33182  out of  33214
Epoch  33183  out of  33214
Epoch  33184  out of  33214
Epoch  33185  out of  33214
Epoch  33186  out of  33214
Epoch  33187  out of  33214
Epoch  33188  out of  33214
Epoch  33189  out of  33214
Epoch  33190  out of  33214
Epoch  33191  out of  33214
Epoch  33192  out of  33214
Epoch  33193  out of  33214
Epoch  33194  out of  33214
Epoch  33195  out of  33214
Epoch  33196  out of  33214
Epoch  33197  out of  33214
Epoch  33198  out of  33214
Epoch  33199  out of  33214
Epoch  33200  out of  33214
Epoch  33201  out of  33214
Epoch  33202  out of  33214
Epoch  33203  out of  33214
Epoch  33204  out of  33214
Epoch  33205  out of  33214
Epoch  33206  out of

Let's use our neural net, trained on half the data, to try to predict the left-out half of data!

In [13]:
print("Should associate each input with its trained output...")
sum_sqr_tot = 0
sum_sqr_res = 0
for i in range(len(xd_test)):
    perm = xd_test[i]

    qsim.reset_all()
    for j in range(in_tot_count):
        if perm[j]:
            qsim.x(j)
    for j in range(out_qubit_count):
        output_layer[j].predict()

    bn = out_bin_count
    offset = 0
    for j in range(out_qubit_count):
        bn = bn // 2
        if qsim.m(in_tot_count + j):
            offset += bn 
    pred = y_bins[offset]

    print("Row: ", str(i))
    print("Input: ", str(perm))
    print("Prediction: ", str(pred))
    print("Observed: ", str(y_test[i]))
    print("Residual: ", str(y_test[i] - pred))
    print()

    sum_sqr_tot += y_test[i] * y_test[i]
    sum_sqr_res += (y_test[i] - pred) * (y_test[i] - pred)

Should associate each input with its trained output...
Row:  0
Input:  [True, True, True, True, True, True, True, True, True, True, True, True]
Prediction:  93.45654296875
Observed:  96.39
Residual:  2.9334570312500006

Row:  1
Input:  [True, True, True, True, True, True, True, True, True, True, True, True]
Prediction:  95.70674072265625
Observed:  95.75
Residual:  0.04325927734375057

Row:  2
Input:  [True, True, True, True, True, True, True, True, True, True, True, True]
Prediction:  95.4626171875
Observed:  95.54
Residual:  0.07738281250000512

Row:  3
Input:  [True, True, True, True, True, True, True, True, True, True, True, False]
Prediction:  93.04392578125
Observed:  94.76
Residual:  1.716074218750009

Row:  4
Input:  [True, True, True, True, True, True, True, True, True, True, False, False]
Prediction:  92.44
Observed:  93.64
Residual:  1.2000000000000028

Row:  5
Input:  [True, True, True, False, True, True, True, True, True, False, True, False]
Prediction:  90.96590087890624


Row:  283
Input:  [False, True, True, False, True, False, False, False, False, False, True, True]
Prediction:  79.29
Observed:  78.3
Residual:  -0.9900000000000091

Row:  284
Input:  [False, True, True, False, True, False, False, False, False, False, True, True]
Prediction:  79.32
Observed:  78.3
Residual:  -1.019999999999996

Row:  285
Input:  [True, False, False, True, True, False, False, False, False, False, True, True]
Prediction:  79.43708251953124
Observed:  78.3
Residual:  -1.1370825195312477

Row:  286
Input:  [False, True, True, False, True, False, False, False, False, False, True, True]
Prediction:  78.99
Observed:  78.3
Residual:  -0.6899999999999977

Row:  287
Input:  [True, False, False, True, True, False, False, False, False, False, True, True]
Prediction:  79.43708251953124
Observed:  78.3
Residual:  -1.1370825195312477

Row:  288
Input:  [True, False, False, True, True, False, False, False, False, False, True, True]
Prediction:  79.42
Observed:  78.3
Residual:  -1.12000

Row:  522
Input:  [False, True, True, True, False, True, True, False, False, False, True, True]
Prediction:  74.0
Observed:  73.26
Residual:  -0.7399999999999949

Row:  523
Input:  [True, False, False, False, False, True, True, False, False, False, True, True]
Prediction:  74.0
Observed:  73.26
Residual:  -0.7399999999999949

Row:  524
Input:  [True, False, True, False, False, True, True, False, False, False, True, True]
Prediction:  74.0
Observed:  73.26
Residual:  -0.7399999999999949

Row:  525
Input:  [False, True, False, False, False, True, True, False, False, False, True, True]
Prediction:  74.0
Observed:  73.26
Residual:  -0.7399999999999949

Row:  526
Input:  [True, False, False, False, False, True, True, False, False, False, True, True]
Prediction:  74.0
Observed:  73.26
Residual:  -0.7399999999999949

Row:  527
Input:  [False, True, True, True, False, True, True, False, False, False, True, True]
Prediction:  74.0
Observed:  73.26
Residual:  -0.7399999999999949

Row:  528
Input

Row:  811
Input:  [True, True, False, False, True, False, False, True, True, False, False, False]
Prediction:  67.06
Observed:  68.1
Residual:  1.039999999999992

Row:  812
Input:  [True, False, True, False, True, False, False, False, True, False, False, False]
Prediction:  75.28599365234375
Observed:  68.0
Residual:  -7.285993652343748

Row:  813
Input:  [True, True, True, True, True, True, True, True, True, True, True, True]
Prediction:  96.4234814453125
Observed:  67.95
Residual:  -28.4734814453125

Row:  814
Input:  [True, False, True, False, False, True, True, True, False, True, True, False]
Prediction:  69.94
Observed:  67.93
Residual:  -2.009999999999991

Row:  815
Input:  [True, True, True, True, True, True, True, False, True, True, True, True]
Prediction:  50.0
Observed:  67.92
Residual:  17.92

Row:  816
Input:  [True, True, True, False, True, True, False, False, True, True, False, False]
Prediction:  68.41
Observed:  67.8
Residual:  -0.6099999999999994

Row:  817
Input:  [Fa

Row:  1053
Input:  [True, False, False, True, True, False, False, False, True, False, False, False]
Prediction:  64.08
Observed:  64.07
Residual:  -0.010000000000005116

Row:  1054
Input:  [True, True, True, True, True, True, False, True, True, True, True, False]
Prediction:  57.73
Observed:  63.91
Residual:  6.18

Row:  1055
Input:  [True, True, False, False, True, True, False, True, True, True, True, False]
Prediction:  58.93
Observed:  63.89
Residual:  4.960000000000001

Row:  1056
Input:  [True, False, True, False, False, True, True, False, False, True, True, False]
Prediction:  66.62
Observed:  63.89
Residual:  -2.730000000000004

Row:  1057
Input:  [True, False, False, True, False, True, True, False, False, True, True, False]
Prediction:  65.95
Observed:  63.89
Residual:  -2.0600000000000023

Row:  1058
Input:  [False, True, True, False, False, True, True, False, False, True, True, False]
Prediction:  65.95
Observed:  63.89
Residual:  -2.0600000000000023

Row:  1059
Input:  [Fals

...

Row:  31938
Input:  [True, False, True, True, True, False, True, True, True, False, True, True]
Prediction:  68.41
Observed:  68.93
Residual:  0.5200000000000102

Row:  31939
Input:  [True, True, True, True, True, True, True, False, True, True, True, False]
Prediction:  68.68
Observed:  68.92
Residual:  0.23999999999999488

Row:  31940
Input:  [True, True, False, True, True, True, False, False, True, True, False, True]
Prediction:  59.6
Observed:  68.92
Residual:  9.32

Row:  31941
Input:  [True, True, True, False, True, True, True, False, True, True, True, False]
Prediction:  77.34
Observed:  68.88
Residual:  -8.460000000000008

Row:  31942
Input:  [True, False, True, True, True, True, False, True, True, True, False, True]
Prediction:  67.76
Observed:  68.84
Residual:  1.0799999999999983

Row:  31943
Input:  [True, True, True, True, True, True, False, True, True, True, False, True]
Prediction:  70.99
Observed:  68.8
Residual:  -2.1899999999999977

Row:  31944
Input:  [True, False, Fal

Row:  32228
Input:  [True, True, False, False, True, True, False, False, True, True, True, True]
Prediction:  37.2828173828125
Observed:  45.26
Residual:  7.977182617187495

Row:  32229
Input:  [True, True, True, True, True, True, False, True, True, True, True, True]
Prediction:  37.02101318359375
Observed:  45.17
Residual:  8.14898681640625

Row:  32230
Input:  [True, True, False, False, True, False, True, False, True, True, False, True]
Prediction:  49.01
Observed:  45.17
Residual:  -3.8399999999999963

Row:  32231
Input:  [True, False, False, True, False, True, True, False, True, False, True, False]
Prediction:  40.58
Observed:  44.87
Residual:  4.289999999999999

Row:  32232
Input:  [True, True, True, False, True, False, True, False, True, True, False, True]
Prediction:  54.49
Observed:  44.84
Residual:  -9.649999999999999

Row:  32233
Input:  [True, True, True, False, True, True, False, False, True, True, True, False]
Prediction:  47.16074951171875
Observed:  44.77
Residual:  -2.3

Row:  32457
Input:  [True, True, False, True, True, True, True, False, True, True, True, True]
Prediction:  32.94
Observed:  69.57
Residual:  36.629999999999995

Row:  32458
Input:  [True, True, True, False, True, True, True, False, True, True, True, False]
Prediction:  77.37
Observed:  69.0
Residual:  -8.370000000000005

Row:  32459
Input:  [True, True, True, True, True, True, True, True, True, True, True, True]
Prediction:  95.4626171875
Observed:  68.68
Residual:  -26.782617187499994

Row:  32460
Input:  [True, True, True, True, True, True, False, True, True, True, True, False]
Prediction:  62.75
Observed:  68.52
Residual:  5.769999999999996

Row:  32461
Input:  [True, True, True, True, True, True, True, True, True, True, True, True]
Prediction:  95.4626171875
Observed:  68.45
Residual:  -27.0126171875

Row:  32462
Input:  [True, True, True, True, True, True, True, True, True, True, True, True]
Prediction:  88.9561474609375
Observed:  68.31
Residual:  -20.6461474609375

Row:  32463


Row:  32745
Input:  [True, True, True, True, True, True, True, True, True, True, True, True]
Prediction:  93.50935791015625
Observed:  65.02
Residual:  -28.489357910156258

Row:  32746
Input:  [True, True, False, True, True, True, True, False, True, True, True, True]
Prediction:  33.24
Observed:  64.62
Residual:  31.380000000000003

Row:  32747
Input:  [True, True, True, True, True, True, True, True, True, True, True, True]
Prediction:  94.9
Observed:  64.58
Residual:  -30.320000000000007

Row:  32748
Input:  [True, False, False, True, False, False, True, True, False, False, True, True]
Prediction:  64.13317138671874
Observed:  64.08
Residual:  -0.053171386718744884

Row:  32749
Input:  [True, False, False, True, True, False, True, False, True, False, True, True]
Prediction:  65.57
Observed:  63.44
Residual:  -2.1299999999999955

Row:  32750
Input:  [True, True, True, True, True, True, True, True, True, True, True, True]
Prediction:  90.6044189453125
Observed:  63.04
Residual:  -27.564

Row:  32974
Input:  [True, False, True, True, True, True, True, False, True, True, True, False]
Prediction:  72.42
Observed:  73.7
Residual:  1.2800000000000011

Row:  32975
Input:  [True, False, True, False, True, True, False, False, True, True, False, False]
Prediction:  75.05
Observed:  73.35
Residual:  -1.7000000000000028

Row:  32976
Input:  [True, True, True, True, True, True, True, True, True, True, True, True]
Prediction:  93.45654296875
Observed:  73.31
Residual:  -20.146542968749998

Row:  32977
Input:  [True, False, True, True, True, True, True, False, True, True, True, False]
Prediction:  68.15
Observed:  73.15
Residual:  5.0

Row:  32978
Input:  [True, True, False, True, True, True, True, True, True, True, True, True]
Prediction:  83.61735595703125
Observed:  73.05
Residual:  -10.567355957031253

Row:  32979
Input:  [True, False, True, True, True, False, True, True, True, False, True, False]
Prediction:  72.21
Observed:  72.8
Residual:  0.5900000000000034

Row:  32980
Inpu

How does this compare to the training R^2 of multiple linear regression?

In [14]:
print("QrackNeuron Validation R^2: ", 1 - sum_sqr_res / sum_sqr_tot)
print("Multiple linear regression validation R^2: ", 1 - ssr / sst)
if (1 - sum_sqr_res / sum_sqr_tot) > (1 - ssr / sst):
    print("QrackNeuron quantum associative memory outperfomed multiple linear regression.")
else:
    print("Multiple linear regression outperfomed QrackNeuron quantum associative memory.")

QrackNeuron Validation R^2:  0.9842410422084613
Multiple linear regression validation R^2:  0.9547922367566187
QrackNeuron quantum associative memory outperfomed multiple linear regression.
